In [ ]:
import math

# Very simple two-parameter, two-objective cost function:
#
# Parameters: x[0], x[1]
#
# Outcomes (minimization objectives):
#    * first element y_0: x[0]*x[0] * (x[1]*x[1] + 1)
#    * second element y_1: (x[0]+1) * (x[0]+x[1])
#
# Contract: Both parameters are positive.
#           (Penalize if contract is violated.)
#
def cost_function(x):
    if x[0] < 0 or x[1] < 0:
        return [math.inf, math.inf]
    else:
        y0 = (x[0]*x[0] + 1) * (x[1]*x[1] + 1)
        y1 = (x[0]-1) * (x[0]+x[1])
        return [y0, y1]

In [ ]:
# examples for what this cost function does

print("cost_function([0, 0]) =", ["%.3f"%y for y in cost_function([0, 0])], end="\n\n")
print("cost_function([1, 0]) =", ["%.3f"%y for y in cost_function([1, 1])], end="\n\n")

print("cost_function([0.2, 0.7]) =", ["%.3f"%y for y in cost_function([0.2, 0.7])])
print("cost_function([0.7, 0.2]) =", ["%.3f"%y for y in cost_function([0.7, 0.2])], end="\n\n")

print("cost_function([0.3, -0.1]) =", cost_function([0.3, -0.1]))

In [ ]:
# the first argument, x, is a list containing the parameter values
# the second argument, w, is a list containing the weights associated with each of the objectives
#
def cost_linear_combination(x, w):
    combined_cost = 0
    y = cost_function(x)
    for i in range(min(len(y), len(w))):
        combined_cost += w[i]*y[i]
    return combined_cost

In [ ]:
# linear combination where both objectives are equally weighted
#
def equal_weight_cost_function(x):
    return cost_linear_combination(x, [1.0, 1.0])

# linear combination where the sum counts double, as compared to the product
#
def unequal_sum_cost_function(x):
    return cost_linear_combination(x, [2.0, 1.0])

for x in [[0, 0], [1, 1], [0.2, 0.7], [0.7, 0.2]]:
    print(["%.2f"%xi for xi in x], ["%.2f"%y for y in cost_function(x)], \
          "%.2f"%equal_weight_cost_function(x), "%.2f"%unequal_sum_cost_function(x), sep="\t\t")

In [ ]:
import scipy.optimize as opt

# minimize each of the two linear combinations
#
init_value = [0.5, 0.5]
precision_x = 1.0e-06

equal_weight_minimum = opt.minimize(equal_weight_cost_function, init_value, \
                                    method='nelder-mead', options={'xatol': precision_x})
print("minimum with equal weights:", ["%.4f"%xi for xi in equal_weight_minimum.x], \
      " -> ", "%.4f"%equal_weight_cost_function(equal_weight_minimum.x), sep="\t")

unequal_sum_minimum = opt.minimize(unequal_sum_cost_function, init_value, \
                                  method='nelder-mead', options={'xatol': precision_x})
print("minimum with unequal weights:", ["%.4f"%xi for xi in unequal_sum_minimum.x], \
      " -> ", "%.4f"%unequal_sum_cost_function(unequal_sum_minimum.x), sep="\t")

In [ ]:
import numpy as np

y0values = []
y1values = []

for k in np.arange(0.1, 1, 0.1):
    def weighted_function(x):
        return cost_linear_combination(x, [k, 1.0-k])
    weighted_minimum = opt.minimize(weighted_function, init_value, \
                                    method='nelder-mead', options={'xatol': precision_x})
    y = cost_function(weighted_minimum.x)
    y0values.append(y[0])
    y1values.append(y[1])
    print("%.2f"%k, ["%.4f"%xi for xi in weighted_minimum.x], "%.4f"%y[0], "%.4f"%y[1], sep="\t")

In [ ]:
# visualize the computed points on the Pareto front

import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(14, 6)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("cost measure y[0]", fontsize=24, color="#322300")
ax.set_ylabel("cost measure y[1]", fontsize=24, color="#322300")

sbn.scatterplot(x=y0values, y=y1values, color="#002855")